In [1]:
import sys

sys.path.append('..')

In [2]:
import os
os.getcwd()

'/mnt/3B1D7BDC2D2641B0/Documents/GIT/SQUAD_NLP/pythonbooks'

In [3]:
os.chdir('..')
os.getcwd()

'/mnt/3B1D7BDC2D2641B0/Documents/GIT/SQUAD_NLP'

# Хочется вытащить все в питонбук, потому что из консоли работать неудобно

# загрузка данных

# Обучение

In [4]:
import numpy as np
import random
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
import torch.optim.lr_scheduler as sched
import torch.utils.data as data
import util

from args import get_train_args
from collections import OrderedDict
from json import dumps
from models import BiDAF
from models_monster import BiDAF_monster
from tensorboardX import SummaryWriter
from tqdm import tqdm
from ujson import load as json_load
from util import collate_fn, SQuAD

In [5]:
train_args = type('', (), {})() # empty "structure" where you can add fields

train_args.train_record_file = './data/train.npz'
train_args.dev_record_file = './data/dev.npz'
train_args.test_record_file = './data/test.npz'
train_args.word_emb_file = './data/word_emb.json'
train_args.char_emb_file = './data/char_emb.json'
train_args.train_eval_file = './data/train_eval.json'
train_args.dev_eval_file = './data/dev_eval.json'
train_args.test_eval_file = './data/test_eval.json'

train_args.name = 'train'       # ???
train_args.max_ans_len = 15     # Maximum length of a predicted answer.
train_args.num_workers = 6      # Number of sub-processes to use per data loader.
train_args.save_dir = './save/' # Base directory for saving information.
train_args.batch_size = 40     # Batch size per GPU. Scales automatically when \
                                #    multiple GPUs are available.
train_args.use_squad_v2 = True  # Whether to use SQuAD 2.0 (unanswerable) questions.
train_args.hidden_size = 120    # Number of features in encoder hidden layers
train_args.num_visuals = 10     # Number of examples to visualize in TensorBoard.
train_args.load_path = None     # Path to load as a model checkpoint.

train_args.eval_steps = 25000   # Number of steps between successive evaluations
train_args.lr = 1.0             # learning rate
train_args.l2_wd = 0.0          # L2 weight decay.
train_args.num_epochs = 30      # Number of epochs for which to train. Negative means forever.
train_args.drop_prob = 0.2      # Probability of zeroing an activation in dropout layers.
train_args.metric_name = 'F1'   # choices=('NLL', 'EM', 'F1'), name of dev metric to determine best checkpoint.
train_args.max_checkpoints = 5  # Maximum number of checkpoints to keep on disk.
train_args.max_grad_norm = 5.0  # Maximum gradient norm for gradient clipping.
train_args.seed = 224           # Random seed
train_args.ema_decay = 0.999    # Decay rate for exponential moving average of parameters.

if train_args.metric_name == 'NLL':
    # Best checkpoint is the one that minimizes negative log-likelihood
    train_args.maximize_metric = False
elif train_args.metric_name in ('EM', 'F1'):
    # Best checkpoint is the one that maximizes EM or F1
    train_args.maximize_metric = True

In [6]:
# from train.py

lambda3 = lambda step: (0.01 + 0.0011 * (step+1)) if step < 2000 else 2.0 if step < 4000 else 0.9999 ** ((step - 4000)//2)

In [7]:
for i in range(95500):
    print(i, ' = ', lambda3(i))

0  =  0.0111
1  =  0.0122
2  =  0.0133
3  =  0.0144
4  =  0.0155
5  =  0.0166
6  =  0.0177
7  =  0.0188
8  =  0.0199
9  =  0.021
10  =  0.0221
11  =  0.0232
12  =  0.024300000000000002
13  =  0.0254
14  =  0.026500000000000003
15  =  0.0276
16  =  0.028700000000000003
17  =  0.0298
18  =  0.030900000000000004
19  =  0.032
20  =  0.033100000000000004
21  =  0.0342
22  =  0.035300000000000005
23  =  0.0364
24  =  0.0375
25  =  0.0386
26  =  0.0397
27  =  0.0408
28  =  0.04190000000000001
29  =  0.043000000000000003
30  =  0.04410000000000001
31  =  0.045200000000000004
32  =  0.0463
33  =  0.047400000000000005
34  =  0.0485
35  =  0.049600000000000005
36  =  0.0507
37  =  0.051800000000000006
38  =  0.0529
39  =  0.054000000000000006
40  =  0.0551
41  =  0.05620000000000001
42  =  0.057300000000000004
43  =  0.05840000000000001
44  =  0.059500000000000004
45  =  0.06060000000000001
46  =  0.061700000000000005
47  =  0.0628
48  =  0.0639
49  =  0.065
50  =  0.0661
51  =  0.0672
52  =  0.0

1149  =  1.2750000000000001
1150  =  1.2761
1151  =  1.2772000000000001
1152  =  1.2783
1153  =  1.2794
1154  =  1.2805000000000002
1155  =  1.2816
1156  =  1.2827000000000002
1157  =  1.2838
1158  =  1.2849000000000002
1159  =  1.286
1160  =  1.2871000000000001
1161  =  1.2882
1162  =  1.2893000000000001
1163  =  1.2904
1164  =  1.2915
1165  =  1.2926000000000002
1166  =  1.2937
1167  =  1.2948000000000002
1168  =  1.2959
1169  =  1.2970000000000002
1170  =  1.2981
1171  =  1.2992000000000001
1172  =  1.3003
1173  =  1.3014000000000001
1174  =  1.3025
1175  =  1.3036
1176  =  1.3047000000000002
1177  =  1.3058
1178  =  1.3069000000000002
1179  =  1.308
1180  =  1.3091000000000002
1181  =  1.3102
1182  =  1.3113000000000001
1183  =  1.3124
1184  =  1.3135000000000001
1185  =  1.3146
1186  =  1.3157
1187  =  1.3168000000000002
1188  =  1.3179
1189  =  1.3190000000000002
1190  =  1.3201
1191  =  1.3212000000000002
1192  =  1.3223
1193  =  1.3234000000000001
1194  =  1.3245
1195  =  1.325

2649  =  2.0
2650  =  2.0
2651  =  2.0
2652  =  2.0
2653  =  2.0
2654  =  2.0
2655  =  2.0
2656  =  2.0
2657  =  2.0
2658  =  2.0
2659  =  2.0
2660  =  2.0
2661  =  2.0
2662  =  2.0
2663  =  2.0
2664  =  2.0
2665  =  2.0
2666  =  2.0
2667  =  2.0
2668  =  2.0
2669  =  2.0
2670  =  2.0
2671  =  2.0
2672  =  2.0
2673  =  2.0
2674  =  2.0
2675  =  2.0
2676  =  2.0
2677  =  2.0
2678  =  2.0
2679  =  2.0
2680  =  2.0
2681  =  2.0
2682  =  2.0
2683  =  2.0
2684  =  2.0
2685  =  2.0
2686  =  2.0
2687  =  2.0
2688  =  2.0
2689  =  2.0
2690  =  2.0
2691  =  2.0
2692  =  2.0
2693  =  2.0
2694  =  2.0
2695  =  2.0
2696  =  2.0
2697  =  2.0
2698  =  2.0
2699  =  2.0
2700  =  2.0
2701  =  2.0
2702  =  2.0
2703  =  2.0
2704  =  2.0
2705  =  2.0
2706  =  2.0
2707  =  2.0
2708  =  2.0
2709  =  2.0
2710  =  2.0
2711  =  2.0
2712  =  2.0
2713  =  2.0
2714  =  2.0
2715  =  2.0
2716  =  2.0
2717  =  2.0
2718  =  2.0
2719  =  2.0
2720  =  2.0
2721  =  2.0
2722  =  2.0
2723  =  2.0
2724  =  2.0
2725  =  2.0

4148  =  0.9926269452909025
4149  =  0.9926269452909025
4150  =  0.9925276825963735
4151  =  0.9925276825963735
4152  =  0.9924284298281139
4153  =  0.9924284298281139
4154  =  0.992329186985131
4155  =  0.992329186985131
4156  =  0.9922299540664326
4157  =  0.9922299540664326
4158  =  0.9921307310710259
4159  =  0.9921307310710259
4160  =  0.9920315179979188
4161  =  0.9920315179979188
4162  =  0.991932314846119
4163  =  0.991932314846119
4164  =  0.9918331216146344
4165  =  0.9918331216146344
4166  =  0.9917339383024729
4167  =  0.9917339383024729
4168  =  0.9916347649086427
4169  =  0.9916347649086427
4170  =  0.9915356014321518
4171  =  0.9915356014321518
4172  =  0.9914364478720087
4173  =  0.9914364478720087
4174  =  0.9913373042272214
4175  =  0.9913373042272214
4176  =  0.9912381704967987
4177  =  0.9912381704967987
4178  =  0.9911390466797491
4179  =  0.9911390466797491
4180  =  0.9910399327750811
4181  =  0.9910399327750811
4182  =  0.9909408287818036
4183  =  0.9909408287818

5815  =  0.9132875152580382
5816  =  0.9131961865065125
5817  =  0.9131961865065125
5818  =  0.9131048668878617
5819  =  0.9131048668878617
5820  =  0.913013556401173
5821  =  0.913013556401173
5822  =  0.9129222550455329
5823  =  0.9129222550455329
5824  =  0.9128309628200284
5825  =  0.9128309628200284
5826  =  0.9127396797237464
5827  =  0.9127396797237464
5828  =  0.912648405755774
5829  =  0.912648405755774
5830  =  0.9125571409151985
5831  =  0.9125571409151985
5832  =  0.9124658852011069
5833  =  0.9124658852011069
5834  =  0.9123746386125868
5835  =  0.9123746386125868
5836  =  0.9122834011487255
5837  =  0.9122834011487255
5838  =  0.9121921728086108
5839  =  0.9121921728086108
5840  =  0.9121009535913298
5841  =  0.9121009535913298
5842  =  0.9120097434959707
5843  =  0.9120097434959707
5844  =  0.9119185425216212
5845  =  0.9119185425216212
5846  =  0.911827350667369
5847  =  0.911827350667369
5848  =  0.9117361679323023
5849  =  0.9117361679323023
5850  =  0.911644994315509

...

87140  =  0.015651197241663868
87141  =  0.015651197241663868
87142  =  0.0156496321219397
87143  =  0.0156496321219397
87144  =  0.01564806715872751
87145  =  0.01564806715872751
87146  =  0.015646502352011635
87147  =  0.015646502352011635
87148  =  0.015644937701776433
87149  =  0.015644937701776433
87150  =  0.015643373208006257
87151  =  0.015643373208006257
87152  =  0.015641808870685458
87153  =  0.015641808870685458
87154  =  0.01564024468979839
87155  =  0.01564024468979839
87156  =  0.015638680665329408
87157  =  0.015638680665329408
87158  =  0.015637116797262877
87159  =  0.015637116797262877
87160  =  0.01563555308558315
87161  =  0.01563555308558315
87162  =  0.015633989530274593
87163  =  0.015633989530274593
87164  =  0.015632426131321566
87165  =  0.015632426131321566
87166  =  0.015630862888708432
87167  =  0.015630862888708432
87168  =  0.01562929980241956
87169  =  0.01562929980241956
87170  =  0.015627736872439322
87171  =  0.015627736872439322
87172  =  0.01562617

88973  =  0.014281183545571945
88974  =  0.014279755427217388
88975  =  0.014279755427217388
88976  =  0.014278327451674667
88977  =  0.014278327451674667
88978  =  0.014276899618929499
88979  =  0.014276899618929499
88980  =  0.014275471928967606
88981  =  0.014275471928967606
88982  =  0.014274044381774709
88983  =  0.014274044381774709
88984  =  0.014272616977336531
88985  =  0.014272616977336531
88986  =  0.014271189715638798
88987  =  0.014271189715638798
88988  =  0.014269762596667235
88989  =  0.014269762596667235
88990  =  0.014268335620407569
88991  =  0.014268335620407569
88992  =  0.014266908786845528
88993  =  0.014266908786845528
88994  =  0.014265482095966843
88995  =  0.014265482095966843
88996  =  0.014264055547757247
88997  =  0.014264055547757247
88998  =  0.014262629142202471
88999  =  0.014262629142202471
89000  =  0.01426120287928825
89001  =  0.01426120287928825
89002  =  0.014259776759000323
89003  =  0.014259776759000323
89004  =  0.014258350781324423
89005  =  

90640  =  0.01313839243885714
90641  =  0.01313839243885714
90642  =  0.013137078599613255
90643  =  0.013137078599613255
90644  =  0.013135764891753294
90645  =  0.013135764891753294
90646  =  0.013134451315264119
90647  =  0.013134451315264119
90648  =  0.013133137870132592
90649  =  0.013133137870132592
90650  =  0.01313182455634558
90651  =  0.01313182455634558
90652  =  0.013130511373889944
90653  =  0.013130511373889944
90654  =  0.013129198322752555
90655  =  0.013129198322752555
90656  =  0.013127885402920281
90657  =  0.013127885402920281
90658  =  0.01312657261437999
90659  =  0.01312657261437999
90660  =  0.013125259957118551
90661  =  0.013125259957118551
90662  =  0.01312394743112284
90663  =  0.01312394743112284
90664  =  0.013122635036379728
90665  =  0.013122635036379728
90666  =  0.013121322772876089
90667  =  0.013121322772876089
90668  =  0.013120010640598801
90669  =  0.013120010640598801
90670  =  0.013118698639534743
90671  =  0.013118698639534743
90672  =  0.0131

92307  =  0.0120882571663943
92308  =  0.012087048340677661
92309  =  0.012087048340677661
92310  =  0.012085839635843592
92311  =  0.012085839635843592
92312  =  0.01208463105188001
92313  =  0.01208463105188001
92314  =  0.01208342258877482
92315  =  0.01208342258877482
92316  =  0.012082214246515944
92317  =  0.012082214246515944
92318  =  0.012081006025091292
92319  =  0.012081006025091292
92320  =  0.012079797924488782
92321  =  0.012079797924488782
92322  =  0.012078589944696334
92323  =  0.012078589944696334
92324  =  0.012077382085701865
92325  =  0.012077382085701865
92326  =  0.012076174347493295
92327  =  0.012076174347493295
92328  =  0.012074966730058546
92329  =  0.012074966730058546
92330  =  0.01207375923338554
92331  =  0.01207375923338554
92332  =  0.012072551857462201
92333  =  0.012072551857462201
92334  =  0.012071344602276456
92335  =  0.012071344602276456
92336  =  0.012070137467816228
92337  =  0.012070137467816228
92338  =  0.012068930454069446
92339  =  0.0120

94140  =  0.011029019263645011
94141  =  0.011029019263645011
94142  =  0.011027916361718647
94143  =  0.011027916361718647
94144  =  0.011026813570082476
94145  =  0.011026813570082476
94146  =  0.011025710888725468
94147  =  0.011025710888725468
94148  =  0.011024608317636596
94149  =  0.011024608317636596
94150  =  0.011023505856804831
94151  =  0.011023505856804831
94152  =  0.011022403506219152
94153  =  0.011022403506219152
94154  =  0.01102130126586853
94155  =  0.01102130126586853
94156  =  0.011020199135741943
94157  =  0.011020199135741943
94158  =  0.011019097115828368
94159  =  0.011019097115828368
94160  =  0.011017995206116786
94161  =  0.011017995206116786
94162  =  0.011016893406596175
94163  =  0.011016893406596175
94164  =  0.011015791717255514
94165  =  0.011015791717255514
94166  =  0.01101469013808379
94167  =  0.01101469013808379
94168  =  0.011013588669069981
94169  =  0.011013588669069981
94170  =  0.011012487310203075
94171  =  0.011012487310203075
94172  =  0.

In [8]:
def main(args):
    # Set up logging and devices
    args.save_dir = util.get_save_dir(args.save_dir, args.name, training=True)
    log = util.get_logger(args.save_dir, args.name)
    tbx = SummaryWriter(args.save_dir)
    device, args.gpu_ids = util.get_available_devices()
    log.info('Args: {}'.format(dumps(vars(args), indent=4, sort_keys=True)))
    args.batch_size *= max(1, len(args.gpu_ids))

    # Set random seed
    log.info('Using random seed {}...'.format(args.seed))
    random.seed(args.seed)
    np.random.seed(args.seed)
    torch.manual_seed(args.seed)
    torch.cuda.manual_seed_all(args.seed)

    # Get embeddings
    log.info('Loading embeddings...')
    word_vectors = util.torch_from_json(args.word_emb_file)

    
    
    # Get data loader
    log.info('Building dataset...')
    train_dataset = SQuAD(args.train_record_file, args.use_squad_v2)
    train_loader = data.DataLoader(train_dataset,
                                   batch_size=args.batch_size,
                                   shuffle=True,
                                   num_workers=args.num_workers,
                                   collate_fn=collate_fn)
    dev_dataset = SQuAD(args.dev_record_file, args.use_squad_v2)
    dev_loader = data.DataLoader(dev_dataset,
                                 batch_size=args.batch_size,
                                 shuffle=False,
                                 num_workers=args.num_workers,
                                 collate_fn=collate_fn)
    
    
    # Get model
    log.info('Building model...')
    model = BiDAF_monster(word_vectors=word_vectors,
                      hidden_size=args.hidden_size,
                      drop_prob=args.drop_prob,
                      char_dict_size=1400,#train_dataset.get_char_dict_size(),
                      char_emb_size=args.hidden_size,
                      conv_kernel_size=3,
                      conv_depth1=50,
                      conv_output_hidden_size=args.hidden_size)
#     model.summary()
    model = nn.DataParallel(model, args.gpu_ids)
    if args.load_path:
        log.info('Loading checkpoint from {}...'.format(args.load_path))
        model, step = util.load_model(model, args.load_path, args.gpu_ids)
    else:
        step = 0
    model = model.to(device)
    model.train()
   
    ema = util.EMA(model, args.ema_decay)

    # Get saver
    saver = util.CheckpointSaver(args.save_dir,
                                 max_checkpoints=args.max_checkpoints,
                                 metric_name=args.metric_name,
                                 maximize_metric=args.maximize_metric,
                                 log=log)

    # Get optimizer and scheduler
    optimizer = optim.Adadelta(model.parameters(), args.lr,
                               weight_decay=args.l2_wd)
    scheduler = sched.LambdaLR(optimizer, lambda3)  # Constant LR

    

    # Train
    log.info('Training...')
    steps_till_eval = args.eval_steps
    steps_till_print_lr = 5000
    epoch = step // len(train_dataset)
    while epoch != args.num_epochs:
        epoch += 1
        log.info('Starting epoch {}...'.format(epoch))
        with torch.enable_grad(), \
                tqdm(total=len(train_loader.dataset)) as progress_bar:
            for cw_idxs, cc_idxs, qw_idxs, qc_idxs, y1, y2, ids in train_loader:
                # Setup for forward
                cw_idxs = cw_idxs.to(device)
                cc_idxs = cc_idxs.to(device)
                qw_idxs = qw_idxs.to(device)
                qc_idxs = qc_idxs.to(device)
                batch_size = cw_idxs.size(0)
                optimizer.zero_grad()

                # Forward
                log_p1, log_p2 = model(cw_idxs, cc_idxs, qw_idxs, qc_idxs)
                y1, y2 = y1.to(device), y2.to(device)
                loss = F.nll_loss(log_p1, y1) + F.nll_loss(log_p2, y2)
                loss_val = loss.item()

                # Backward
                loss.backward()
                nn.utils.clip_grad_norm_(model.parameters(), args.max_grad_norm)
                optimizer.step()
                scheduler.step()
                
                
                ema(model, step // batch_size)

                # Log info
                step += batch_size
                progress_bar.update(batch_size)
                progress_bar.set_postfix(epoch=epoch,
                                         NLL=loss_val)
                tbx.add_scalar('train/NLL', loss_val, step)
                tbx.add_scalar('train/LR',
                               optimizer.param_groups[0]['lr'],
                               step)

                steps_till_eval -= batch_size
                
                steps_till_print_lr -= batch_size
                if steps_till_print_lr <= 0:
                    print('Learning rate: ', end='')
                    for param_group in optimizer.param_groups:
                        print(param_group['lr'])
                    steps_till_print_lr = 5000
                if steps_till_eval <= 0:
                    steps_till_eval = args.eval_steps

                    # Evaluate and save checkpoint
                    log.info('Evaluating at step {}...'.format(step))
                    #ema.assign(model)
                    results, pred_dict = evaluate(model, dev_loader, device,
                                                  args.dev_eval_file,
                                                  args.max_ans_len,
                                                  args.use_squad_v2)
                    saver.save(step, model, results[args.metric_name], device)
                    #ema.resume(model)

                    # Log to console
                    results_str = ', '.join('{}: {:05.2f}'.format(k, v)
                                            for k, v in results.items())
                    log.info('Dev {}'.format(results_str))

                    # Log to TensorBoard
                    log.info('Visualizing in TensorBoard...')
                    for k, v in results.items():
                        tbx.add_scalar('dev/{}'.format(k), v, step)
                    util.visualize(tbx,
                                   pred_dict=pred_dict,
                                   eval_path=args.dev_eval_file,
                                   step=step,
                                   split='dev',
                                   num_visuals=args.num_visuals)

In [9]:
def evaluate(model, data_loader, device, eval_file, max_len, use_squad_v2):
    nll_meter = util.AverageMeter()

    model.eval()
    pred_dict = {}
    with open(eval_file, 'r') as fh:
        gold_dict = json_load(fh)
    with torch.no_grad(), \
            tqdm(total=len(data_loader.dataset)) as progress_bar:
        for cw_idxs, cc_idxs, qw_idxs, qc_idxs, y1, y2, ids in data_loader:
            # Setup for forward
            cw_idxs = cw_idxs.to(device)
            cc_idxs = cc_idxs.to(device)
            qw_idxs = qw_idxs.to(device)
            qc_idxs = qc_idxs.to(device)
            batch_size = cw_idxs.size(0)

            # Forward
            log_p1, log_p2 = model(cw_idxs, cc_idxs, qw_idxs, qc_idxs)
            y1, y2 = y1.to(device), y2.to(device)
            loss = F.nll_loss(log_p1, y1) + F.nll_loss(log_p2, y2)
            nll_meter.update(loss.item(), batch_size)

            # Get F1 and EM scores
            p1, p2 = log_p1.exp(), log_p2.exp()
            starts, ends = util.discretize(p1, p2, max_len, use_squad_v2)

            # Log info
            progress_bar.update(batch_size)
            progress_bar.set_postfix(NLL=nll_meter.avg)

            preds, _ = util.convert_tokens(gold_dict,
                                           ids.tolist(),
                                           starts.tolist(),
                                           ends.tolist(),
                                           use_squad_v2)
            pred_dict.update(preds)

    model.train()

    results = util.eval_dicts(gold_dict, pred_dict, use_squad_v2)
    results_list = [('NLL', nll_meter.avg),
                    ('F1', results['F1']),
                    ('EM', results['EM'])]
    if use_squad_v2:
        results_list.append(('AvNA', results['AvNA']))
    results = OrderedDict(results_list)

    return results, pred_dict

In [10]:
main(train_args)

[05.11.19 07:21:11] Args: {
    "batch_size": 40,
    "char_emb_file": "./data/char_emb.json",
    "dev_eval_file": "./data/dev_eval.json",
    "dev_record_file": "./data/dev.npz",
    "drop_prob": 0.2,
    "ema_decay": 0.999,
    "eval_steps": 25000,
    "gpu_ids": [
        0
    ],
    "hidden_size": 120,
    "l2_wd": 0.0,
    "load_path": null,
    "lr": 1.0,
    "max_ans_len": 15,
    "max_checkpoints": 5,
    "max_grad_norm": 5.0,
    "maximize_metric": true,
    "metric_name": "F1",
    "name": "train",
    "num_epochs": 30,
    "num_visuals": 10,
    "num_workers": 6,
    "save_dir": "./save/train/train-28",
    "seed": 224,
    "test_eval_file": "./data/test_eval.json",
    "test_record_file": "./data/test.npz",
    "train_eval_file": "./data/train_eval.json",
    "train_record_file": "./data/train.npz",
    "use_squad_v2": true,
    "word_emb_file": "./data/word_emb.json"
}
[05.11.19 07:21:11] Using random seed 224...
[05.11.19 07:21:11] Loading embeddings...
[05.11.19 07:21:

  0%|          | 0/129922 [00:00<?, ?it/s]

[05.11.19 07:22:15] Saver will maximize F1...
[05.11.19 07:22:15] Training...
[05.11.19 07:22:15] Starting epoch 1...


  4%|▍         | 5000/129922 [01:29<37:17, 55.84it/s, NLL=6.72, epoch=1] 

Learning rate: 0.14750000000000002


...

Learning rate: 0.0697084890943537


 66%|██████▋   | 86360/129922 [26:28<12:31, 57.95it/s, NLL=2.64, epoch=18]

Learning rate: 0.06927761201700662


 67%|██████▋   | 87520/129922 [26:50<13:39, 51.74it/s, NLL=2.75, epoch=18]Traceback (most recent call last):
Traceback (most recent call last):
  File "/home/celidos/anaconda3/envs/venv_tensorflowgpu/lib/python3.6/multiprocessing/queues.py", line 240, in _feed
    send_bytes(obj)
  File "/home/celidos/anaconda3/envs/venv_tensorflowgpu/lib/python3.6/multiprocessing/connection.py", line 200, in send_bytes
    self._send_bytes(m[offset:offset + size])
  File "/home/celidos/anaconda3/envs/venv_tensorflowgpu/lib/python3.6/multiprocessing/connection.py", line 404, in _send_bytes
    self._send(header + buf)
  File "/home/celidos/anaconda3/envs/venv_tensorflowgpu/lib/python3.6/multiprocessing/connection.py", line 368, in _send
    n = write(self._handle, buf)
BrokenPipeError: [Errno 32] Broken pipe
  File "/home/celidos/anaconda3/envs/venv_tensorflowgpu/lib/python3.6/multiprocessing/queues.py", line 240, in _feed
    send_bytes(obj)
  File "/home/celidos/anaconda3/envs/venv_tensorflowgpu/lib/

KeyboardInterrupt: 

In [ ]:
torch.backends.cudnn.version()

# посмотрим, из чего состоят cc_idxs

In [ ]:
train_dataset = SQuAD(train_args.train_record_file, train_args.use_squad_v2)
train_loader = data.DataLoader(train_dataset,
                               batch_size=train_args.batch_size,
                               shuffle=True,
                               num_workers=train_args.num_workers,
                               collate_fn=collate_fn)

In [ ]:
train_dataset.get_char_dict_size()

In [ ]:
jjj = 0
cset1 = set()
cset2 = set()
for cw_idxs, cc_idxs, qw_idxs, qc_idxs, y1, y2, ids in train_loader:
    jjj += 1
#     print(cc_idxs.shape)
#     print(cc_idxs.numpy())
    cset1 |= set(cc_idxs.numpy().ravel())
    cset2 |= set(qc_idxs.numpy().ravel())
#     print(cc_idxs[0, 1, :])
#     if jjj > 100:
#         break

In [ ]:
''.join([str(x) + ' ' for x in list(cset1)])

In [24]:
''.join([str(x) + ' ' for x in list(cset2)])

'0 1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 22 534 535 25 538 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71 72 73 74 75 523 77 78 79 80 81 594 82 76 83 86 87 88 89 84 91 604 85 90 1110 94 609 528 527 101 102 104 105 106 107 108 109 110 111 112 113 114 115 628 117 119 631 120 122 121 642 131 646 139 140 653 143 144 655 146 661 662 663 1175 1176 163 165 166 542 167 678 172 176 516 189 517 220 230 231 1274 253 259 260 262 263 1288 265 266 1289 1292 1291 270 1290 272 273 276 279 282 290 291 810 303 306 309 310 311 312 825 313 321 322 324 325 326 327 329 330 331 332 333 334 336 340 343 345 348 1372 1374 1375 353 355 356 359 360 361 366 367 373 379 384 587 589 409 590 591 1100 422 423 424 440 441 442 443 478 479 480 481 483 486 1002 498 501 '

# тест

In [22]:
aaaa = np.array([[0, 1], [1, 2]]).ravel().tolist()

In [23]:
aaaa

[0, 1, 1, 2]

In [24]:
set(aaaa)

{0, 1, 2}

In [5]:
util.get_available_devices()

(device(type='cuda', index=0), [0])

# тест2

In [6]:
device, train_args.gpu_ids = util.get_available_devices()

In [7]:
device, train_args.gpu_ids

(device(type='cuda', index=0), [0])

In [10]:
A = torch.rand((19456, 1, 16, 100)).to(device)

In [12]:
B = nn.Conv2d(in_channels = 1, 
                out_channels = 72, 
                kernel_size = (3, 100),
                padding=[1, 0]).cuda()(A)

In [13]:
B

tensor([[[[-0.2982],
          [-0.2431],
          [-0.7081],
          ...,
          [-0.7422],
          [-0.6618],
          [-0.3046]],

         [[ 0.0683],
          [-0.0804],
          [-0.0250],
          ...,
          [ 0.1863],
          [-0.1117],
          [-0.1203]],

         [[-0.3199],
          [-0.1380],
          [-0.1947],
          ...,
          [-0.0441],
          [-0.3234],
          [-0.0039]],

         ...,

         [[-0.0629],
          [ 0.1735],
          [-0.1044],
          ...,
          [-0.3480],
          [ 0.0234],
          [ 0.2862]],

         [[-0.2767],
          [-0.3573],
          [-0.6291],
          ...,
          [-0.4452],
          [-0.4202],
          [-0.4769]],

         [[ 0.2735],
          [ 0.4395],
          [ 0.2507],
          ...,
          [ 0.1173],
          [ 0.3946],
          [ 0.0975]]],


        [[[-0.2974],
          [-0.4128],
          [-0.4716],
          ...,
          [-0.4754],
          [-0.5159],
     